In [4]:
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
from bs4 import BeautifulSoup
import json
from geopy.geocoders import Nominatim
import requests
from pandas.io.json import json_normalize
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
import folium

print('Libraries imported.')

Libraries imported.


## Web scraping the data of Toronto neighbourhoods

### Requesting HTML data from the associated link and finding the table

In [5]:
html_data = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M')

In [6]:
soup = BeautifulSoup(html_data.content,'html.parser')

In [9]:
table = soup.find_all('table')
canada = pd.read_html(str(table))[0]
canada.head()

Postal Code           Borough              Neighbourhood
0         M1A      Not assigned               Not assigned
1         M2A      Not assigned               Not assigned
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront

In [11]:
canada.rename(columns={'Postal Code' : 'PostalCode'}, inplace=True)

### Removing Borough values that are 'Not Assigned', as well as assigning Borough values to the Neighbourhood values which are 'Not Assigned' 

In [12]:
canada = canada[canada.Borough != 'Not assigned']
canada.loc[canada['Neighbourhood'] =='Not assigned' , 'Neighbourhood'] = canada['Borough']

In [13]:
result = canada.groupby(['PostalCode','Borough']).agg( ', '.join)
canada_new=result.reset_index()
canada_new.head()

PostalCode      Borough                           Neighbourhood
0        M1B  Scarborough                          Malvern, Rouge
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek
2        M1E  Scarborough       Guildwood, Morningside, West Hill
3        M1G  Scarborough                                  Woburn
4        M1H  Scarborough                               Cedarbrae

### Importing GeoSpace data and merging it with the initial dataframe

In [15]:
df_coor = pd.read_csv('coordinates.csv')
df_coor.rename(columns={'Postal Code' : 'PostalCode'}, inplace=True)
df_coor.head()

PostalCode   Latitude  Longitude
0        M1B  43.806686 -79.194353
1        M1C  43.784535 -79.160497
2        M1E  43.763573 -79.188711
3        M1G  43.770992 -79.216917
4        M1H  43.773136 -79.239476

In [73]:
toronto_df = pd.merge(canada_new, df_coor[['PostalCode','Latitude', 'Longitude']], on='PostalCode')
toronto_df.head()

PostalCode      Borough                           Neighbourhood   Latitude  \
0        M1B  Scarborough                          Malvern, Rouge  43.806686   
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.784535   
2        M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3        M1G  Scarborough                                  Woburn  43.770992   
4        M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

## Obtaining location data using Foursquare API

### Initial mapping of Toronto and the neighbourhoods

In [75]:
address = 'Toronto, ON'

geolocator = Nominatim(user_agent="toronto_explore")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [76]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

for lat, lng, borough, neighbourhood in zip(toronto_df['Latitude'], toronto_df['Longitude'], toronto_df['Borough'], toronto_df['Neighbourhood']):
    label = '{}, {}'.format(neighbourhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

### Define client credentials

In [77]:
CLIENT_ID = '42OERA1R25Y1FZB4GHLTM3NJH3PSUC1MPA2G3EAFRNLIYTJN' # your Foursquare ID
CLIENT_& (toronto_merged['Venue Category'] == 'Chinese Restaurant') ]& (toronto_merged['Venue Category'] == 'Chinese Restaurant') ]& (toronto_merged['Venue Category'] == 'Chinese Restaurant') ]& (toronto_merged['Venue Category'] == 'Chinese Restaurant') ]& (toronto_merged['Venue Category'] == 'Chinese Restaurant') ]### Define client credentialsSECRET = 'QRL5FASL3JZLD2QFG0HPWHYMBF55WAANFM42JFUQ3TN01RLR' # your Foursquare Secret
VERSION = '20210224' # Foursquare API version
radius=500
LIMIT=100

### Defining a function to obtain nearby location data (venues) of all neighbourhoods

In [78]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)### Define client credentials

In [79]:
toronto_venues = getNearbyVenues(names=toronto_df['Neighbourhood'],
                                   latitudes=toronto_df['Latitude'],
                                   longitudes=toronto_df['Longitude']
                                  )

Malvern, Rouge
Rouge Hill, Port Union, Highland Creek
Guildwood, Morningside, West Hill
Woburn
Cedarbrae
Scarborough Village
Kennedy Park, Ionview, East Birchmount Park
Golden Mile, Clairlea, Oakridge
Cliffside, Cliffcrest, Scarborough Village West
Birch Cliff, Cliffside West
Dorset Park, Wexford Heights, Scarborough Town Centre
Wexford, Maryvale
Agincourt
Clarks Corners, Tam O'Shanter, Sullivan
Milliken, Agincourt North, Steeles East, L'Amoreaux East
Steeles West, L'Amoreaux West
Upper Rouge
Hillcrest Village
Fairview, Henry Farm, Oriole
Bayview Village
York Mills, Silver Hills
Willowdale, Newtonbrook
Willowdale, Willowdale East
York Mills West
Willowdale, Willowdale West
Parkwoods
Don Mills
Don Mills
Bathurst Manor, Wilson Heights, Downsview North
Northwood Park, York University
Downsview
Downsview
Downsview
Downsview
Victoria Village
Parkview Hill, Woodbine Gardens
Woodbine Heights
The Beaches
Leaside
Thorncliffe Park
East Toronto, Broadview North (Old East York)
The Danforth West, 

In [80]:
toronto_venues.groupby('Neighbourhood').count()

Neighbourhood Latitude  \
Neighbourhood                                                                
Agincourt                                                                4   
Alderwood, Long Branch                                                   7   
Bathurst Manor, Wilson Heights, Downsview North                         19   
Bayview Village                                                          4   
Bedford Park, Lawrence Manor East                                       25   
Berczy Park                                                             58   
Birch Cliff, Cliffside West                                              4   
Brockton, Parkdale Village, Exhibition Place                            23   
Business reply mail Processing Centre, South Ce...                      18   
CN Tower, King and Spadina, Railway Lands, Harb...                      13   
Caledonia-Fairbanks                                                      4   
Canada Post Gateway Processing Centre                                   14   
Cedarbrae                                                                9   
Central Bay Street                                                      61   
Christie                                                                16   
Church and Wellesley                                                    79   
Clarks Corners, Tam O'Shanter, Sullivan                                 14   
Cliffside, Cliffcrest, Scarborough Village West                          2   
Commerce Court, Victoria Hotel                                         100   
Davisville                                                              37   
Davisville North                                                         8   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                         5   
Don Mills                                                               26   
Dorset Park, Wexford Heights, Scarborough Town ...                       5   
Downsview                                                               15   
Dufferin, Dovercourt Village                                            15   
East Toronto, Broadview North (Old East York)                            3   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                      10   
Fairview, Henry Farm, Oriole                                            64   
First Canadian Place, Underground city                                 100   
Forest Hill North & West, Forest Hill Road Park                          4   
Garden District, Ryerson                                               100   
Glencairn                                                                5   
Golden Mile, Clairlea, Oakridge                                          8   
Guildwood, Morningside, West Hill                                        8   
Harbourfront East, Union Station, Toronto Islands                      100   
High Park, The Junction South                                           26   
Hillcrest Village                                                        5   
Humber Summit                                                            2   
Humberlea, Emery                                                         2   
Humewood-Cedarvale                                                       3   
India Bazaar, The Beaches West                                          20   
Islington Avenue, Humber Valley Village                                  1   
Kennedy Park, Ionview, East Birchmount Park                              4   
Kensington Market, Chinatown, Grange Park                               65   
Kingsview Village, St. Phillips, Martin Grove G...                       4   
Lawrence Manor, Lawrence Heights                                        14   
Lawrence Park                                                            4   
Leaside                                                                 31   
Little Portugal, Trinity                                                42

In [81]:
toronto_venues['Venue Category'].unique()[:100]

array(['Fast Food Restaurant', 'Bar', 'Bank', 'Electronics Store',
       'Restaurant', 'Mexican Restaurant', 'Rental Car Location',
       'Medical Center', 'Intersection', 'Breakfast Spot', 'Coffee Shop',
       'Korean BBQ Restaurant', 'Soccer Field', 'Caribbean Restaurant',
       'Hakka Restaurant', 'Thai Restaurant', 'Athletics & Sports',
       'Bakery', 'Gas Station', 'Lounge', 'Fried Chicken Joint',
       'Playground', 'Cosmetics Shop', 'Department Store', 'Hobby Shop',
       'Discount Store', 'Ice Cream Shop', 'Bus Line', 'Metro Station',
       'Bus Station', 'Motel', 'American Restaurant', 'Café',
       'General Entertainment', 'Skating Rink', 'College Stadium',
       'Chinese Restaurant', 'Indian Restaurant', 'Vietnamese Restaurant',
       'Pet Store', 'Sandwich Place', 'Middle Eastern Restaurant',
       'Auto Garage', 'Accessories Store', 'Latin American Restaurant',
       'Clothing Store', 'Italian Restaurant', 'Noodle House',
       'Pizza Place', 'Pharmacy', 'Co

### Finding out presence of Chinese restaurants

In [82]:
"Chinese Restaurant" in toronto_venues['Venue Category'].unique()

True

### Analyzing each neighbourhood. Group rows by neighborhood and by taking the mean of the frequency of occurrence of each venue category

In [83]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neigh### Define client credentialsborhood column back to dataframe
toronto_onehot['Neighbourhood'] = toronto_venues['Neighbourhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]
toronto_onehot.head()

Neighbourhood  Accessories Store  Adult Boutique  \
0                          Malvern, Rouge                  0               0   
1  Rouge Hill, Port Union, Highland Creek                  0               0   
2       Guildwood, Morningside, West Hill                  0               0   
3       Guildwood, Morningside, West Hill                  0               0   
4       Guildwood, Morningside, West Hill                  0               0   

   Airport  Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0        0                   0             0               0                0   
1        0                   0             0               0                0   
2        0                   0             0               0                0   
3        0                   0             0               0                0   
4        0                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auto Garage  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0              0          0           0           0       0   
1            0              0          0           0           0       0   
2            0              0          0           0           0       0   
3            0              0          0           0           0       0   
4            0              0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0     0    0               0                 0                 0   
1     0    1               0                 0                 0   
2     1    0               0                 0                 0   
3     0    0               0                 0                 0   
4     0    0               0                 0                 0   

   Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  Beer Store  \
0                   0      0                0         0           0   
1                   0      0                0         0           0   
2                   0      0                0         0           0   
3                   0      0                0         0           0   
4                   0      0                0         0           0   

   Belgian Restaurant  Bike Shop  Bistro  Boat or Ferry  Bookstore  Boutique  \
0                   0          0       0              0          0         0   
1                   0          0       0              0          0         0   
2                   0          0       0              0          0         0   
3                   0          0       0              0          0         0   
4                   0          0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                

In [84]:
toronto_grouped = toronto_onehot.groupby('Neighbourhood').mean().reset_index()
print(toronto_grouped.shape)
toronto_grouped

(96, 269)


Neighbourhood  Accessories Store  \
0                                           Agincourt           0.000000   
1                              Alderwood, Long Branch           0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North           0.000000   
3                                     Bayview Village           0.000000   
4                   Bedford Park, Lawrence Manor East           0.000000   
5                                         Berczy Park           0.000000   
6                         Birch Cliff, Cliffside West           0.000000   
7        Brockton, Parkdale Village, Exhibition Place           0.000000   
8   Business reply mail Processing Centre, South C...           0.000000   
9   CN Tower, King and Spadina, Railway Lands, Har...           0.000000   
10                                Caledonia-Fairbanks           0.000000   
11              Canada Post Gateway Processing Centre           0.000000   
12                                          Cedarbrae           0.000000   
13                                 Central Bay Street           0.000000   
14                                           Christie           0.000000   
15                               Church and Wellesley           0.000000   
16            Clarks Corners, Tam O'Shanter, Sullivan           0.000000   
17    Cliffside, Cliffcrest, Scarborough Village West           0.000000   
18                     Commerce Court, Victoria Hotel           0.000000   
19                                         Davisville           0.000000   
20                                   Davisville North           0.000000   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn           0.000000   
22                                          Don Mills           0.000000   
23  Dorset Park, Wexford Heights, Scarborough Town...           0.000000   
24                                          Downsview           0.000000   
25                       Dufferin, Dovercourt Village           0.000000   
26      East Toronto, Broadview North (Old East York)           0.000000   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...           0.000000   
28                       Fairview, Henry Farm, Oriole           0.000000   
29             First Canadian Place, Underground city           0.000000   
30    Forest Hill North & West, Forest Hill Road Park           0.000000   
31                           Garden District, Ryerson           0.000000   
32                                          Glencairn           0.000000   
33                    Golden Mile, Clairlea, Oakridge           0.000000   
34                  Guildwood, Morningside, West Hill           0.000000   
35  Harbourfront East, Union Station, Toronto Islands           0.000000   
36                      High Park, The Junction South           0.000000   
37                                  Hillcrest Village           0.000000   
38                                      Humber Summit           0.000000   
39                                   Humberlea, Emery           0.000000   
40                                 Humewood-Cedarvale           0.000000   
41                     India Bazaar, The Beaches West           0.000000   
42            Islington Avenue, Humber Valley Village           0.000000   
43        Kennedy Park, Ionview, East Birchmount Park           0.000000   
44          Kensington Market, Chinatown, Grange Park           0.000000   
45  Kingsview Village, St. Phillips, Martin Grove ...           0.000000   
46                   Lawrence Manor, Lawrence Heights           0.071429   
47                                      Lawrence Park           0.000000   
48                                            Leaside           0.000000   
49                           Little Portugal, Trinity           0.000000   
50                                     Malvern, Rouge           0.000000   
51  Milliken, Agincourt North, Steeles East, L'Amo...           0.000000   
52  Mimico N

### Justifying the dataframe to specifically Chinese restaurants

In [85]:
len(toronto_grouped[toronto_grouped["Chinese Restaurant"] > 0])

12

In [86]:
toronto_chinese = toronto_grouped[["Neighbourhood","Chinese Restaurant"]]
toronto_chinese.head()

Neighbourhood  Chinese Restaurant
0                                        Agincourt                0.00
1                           Alderwood, Long Branch                0.00
2  Bathurst Manor, Wilson Heights, Downsview North                0.00
3                                  Bayview Village                0.25
4                Bedford Park, Lawrence Manor East                0.00

## Clustering

### Creating the model

In [87]:
# set number of clusters
kclusters = 3

toronto_grouped_clustering = toronto_chinese.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:20]

array([0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0])

In [88]:
toronto_merged = toronto_chinese.copy()
toronto_merged["Cluster Labels"] = kmeans.labels_
toronto_merged = toronto_merged.join(toronto_venues.set_index('Neighbourhood'), on='Neighbourhood')
toronto_merged.sort_values(["Cluster Labels"], inplace=True)
toronto_merged.head()

Neighbourhood  Chinese Restaurant  Cluster Labels  \
0                  Agincourt                 0.0               0   
65  Richmond, Adelaide, King                 0.0               0   
65  Richmond, Adelaide, King                 0.0               0   
65  Richmond, Adelaide, King                 0.0               0   
65  Richmond, Adelaide, King                 0.0               0   

    Neighbourhood Latitude  Neighbourhood Longitude  \
0                43.794200               -79.262029   
65               43.650571               -79.384568   
65               43.650571               -79.384568   
65               43.650571               -79.384568   
65               43.650571               -79.384568   

                          Venue  Venue Latitude  Venue Longitude  \
0   Panagio's Breakfast & Lunch       43.792370       -79.260203   
65          Daily Press Juicery       43.650388       -79.388792   
65              HotBlack Coffee       43.650364       -79.388669   
65                          Pai       43.647923       -79.388579   
65          Brick Street Bakery       43.648815       -79.380605   

     Venue Category  
0    Breakfast Spot  
65        Juice Bar  
65      Coffee Shop  
65  Thai Restaurant  
65           Bakery

### Mapping the clusters

In [96]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Neighbourhood Latitude'], toronto_merged['Neighbourhood Longitude'], toronto_merged['Neighbourhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### Analyzing each cluster

Cluster 1

In [90]:
toronto_merged.loc[(toronto_merged['Cluster Labels'] == 0) & (toronto_merged['Venue Category'] == 'Chinese Restaurant') ]

Neighbourhood  Chinese Restaurant  \
84           Toronto Dominion Centre, Design Exchange            0.010000   
74                        St. James Town, Cabbagetown            0.022727   
31                           Garden District, Ryerson            0.010000   
35  Harbourfront East, Union Station, Toronto Islands            0.010000   
28                       Fairview, Henry Farm, Oriole            0.015625   
22                                          Don Mills            0.038462   

    Cluster Labels  Neighbourhood Latitude  Neighbourhood Longitude  \
84               0               43.647177               -79.381576   
74               0               43.667967               -79.367675   
31               0               43.657162               -79.378937   
35               0               43.640816               -79.381752   
28               0               43.778517               -79.346556   
22               0               43.725900               -79.340923   

                     Venue  Venue Latitude  Venue Longitude  \
84        Szechuan Express       43.646973       -79.379549   
74           China Gourmet       43.664180       -79.368359   
31  GB Hand-Pulled Noodles       43.656434       -79.383783   
35      Pearl Harbourfront       43.638157       -79.380688   
28              Manchu Wok       43.778225       -79.343302   
22        Congee Star 帝王名粥       43.726586       -79.341833   

        Venue Category  
84  Chinese Restaurant  
74  Chinese Restaurant  
31  Chinese Restaurant  
35  Chinese Restaurant  
28  Chinese Restaurant  
22  Chinese Restaurant

Cluster 2

In [91]:
toronto_merged.loc[(toronto_merged['Cluster Labels'] == 1) & (toronto_merged['Venue Category'] == 'Chinese Restaurant') ]

Neighbourhood  Chinese Restaurant  \
23  Dorset Park, Wexford Heights, Scarborough Town...                0.20   
3                                     Bayview Village                0.25   

    Cluster Labels  Neighbourhood Latitude  Neighbourhood Longitude  \
23               1               43.757410               -79.273304   
3                1               43.786947               -79.385975   

                            Venue  Venue Latitude  Venue Longitude  \
23             Kim Kim restaurant       43.753833       -79.276611   
3   Sun Star Chinese Cuisine 翠景小炒       43.787914       -79.381234   

        Venue Category  
23  Chinese Restaurant  
3   Chinese Restaurant

Cluster 3

In [92]:
toronto_merged.loc[(toronto_merged['Cluster Labels'] == 2) & (toronto_merged['Venue Category'] == 'Chinese Restaurant') ]

Neighbourhood  Chinese Restaurant  \
87                                Westmount            0.125000   
56        North Toronto West, Lawrence Park            0.058824   
16  Clarks Corners, Tam O'Shanter, Sullivan            0.071429   
75            Steeles West, L'Amoreaux West            0.090909   

    Cluster Labels  Neighbourhood Latitude  Neighbourhood Longitude  \
87               2               43.696319               -79.532242   
56               2               43.715383               -79.405678   
16               2               43.781638               -79.304302   
75               2               43.799525               -79.318389   

                                 Venue  Venue Latitude  Venue Longitude  \
87              Mayflower Chinese Food       43.692753       -79.531566   
56                           C'est Bon       43.716785       -79.400406   
16  The Royal Chinese Restaurant 避風塘小炒       43.780505       -79.298844   
75       Mr Congee Chinese Cuisine 龍粥記       43.798879       -79.318335   

        Venue Category  
87  Chinese Restaurant  
56  Chinese Restaurant  
16  Chinese Restaurant  
75  Chinese Restaurant

## Main findings

Ranking of clusters with most Chinese restaurants to least Chinese restaurants: Cluster 2, Cluster 3, Cluster 1